In [39]:
import numpy as np
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from mpl_toolkits.axes_grid1 import make_axes_locatable

def plot_blackjack_values(V):

    def get_Z(x, y, usable_ace):
        if (x,y,usable_ace) in V:
            return V[x,y,usable_ace]
        else:
            return 0

    def get_figure(usable_ace, ax):
        x_range = np.arange(11, 22)
        y_range = np.arange(1, 11)
        X, Y = np.meshgrid(x_range, y_range)
        
        Z = np.array([get_Z(x,y,usable_ace) for x,y in zip(np.ravel(X), np.ravel(Y))]).reshape(X.shape)

        surf = ax.plot_surface(X, Y, Z, rstride=1, cstride=1, cmap=plt.cm.coolwarm, vmin=-1.0, vmax=1.0)
        ax.set_xlabel('Player\'s Current Sum')
        ax.set_ylabel('Dealer\'s Showing Card')
        ax.set_zlabel('State Value')
        ax.view_init(ax.elev, -120)

    fig = plt.figure(figsize=(40, 40))
    ax = fig.add_subplot(211, projection='3d')
    ax.set_title('Usable Ace')
    get_figure(True, ax)
    ax = fig.add_subplot(212, projection='3d')
    ax.set_title('No Usable Ace')
    get_figure(False, ax)
    plt.show()

def plot_policy(policy):

    def get_Z(x, y, usable_ace):
        if (x,y,usable_ace) in policy:
            return policy[x,y,usable_ace]
        else:
            return 1

    def get_figure(usable_ace, ax):
        x_range = np.arange(11, 22)
        y_range = np.arange(10, 0, -1)
        X, Y = np.meshgrid(x_range, y_range)
        Z = np.array([[get_Z(x,y,usable_ace) for x in x_range] for y in y_range])
        surf = ax.imshow(Z, cmap=plt.get_cmap('Pastel2', 2), vmin=0, vmax=1, extent=[10.5, 21.5, 0.5, 10.5])
        plt.xticks(x_range)
        plt.yticks(y_range)
        plt.gca().invert_yaxis()
        ax.set_xlabel('Player\'s Current Sum')
        ax.set_ylabel('Dealer\'s Showing Card')
        ax.grid(color='w', linestyle='-', linewidth=1)
        divider = make_axes_locatable(ax)
        cax = divider.append_axes("right", size="5%", pad=0.1)
        cbar = plt.colorbar(surf, ticks=[0,1], cax=cax)
        cbar.ax.set_yticklabels(['0 (STICK)','1 (HIT)'])
            
    fig = plt.figure(figsize=(15, 15))
    ax = fig.add_subplot(121)
    ax.set_title('Usable Ace')
    get_figure(True, ax)
    ax = fig.add_subplot(122)
    ax.set_title('No Usable Ace')
    get_figure(False, ax)
    plt.show()

# Monte Carlo Methods
In this notebook, you will write your own implementations of many Monte Carlo(MC) algorithms.
While we have provided some starter code, you are welcome to erase these hints and write code from scratch

## Part 0: Explore BlackjackEnv
We begin by importing the necessary packages.

In [26]:
import sys
import gym
import numpy as np
from collections import defaultdict

Use the code cell below to create an instance of the Blackjack environment.

In [27]:
env = gym.make('Blackjack-v0')

In [28]:
print(env.observation_space)

Tuple(Discrete(32), Discrete(11), Discrete(2))


In [29]:
print(env.action_space)

Discrete(2)


In [30]:
for i_episode in range(3):
  state = env.reset()
  while True:
    print(state)
    action = env.action_space.sample()
    state, reward, done, info = env.step(action)
    if done:
      print('End game! Reward: ', reward)
      print('You won :)\n') if reward > 0 else print('You lost :(\n')
      break

(7, 3, False)
(17, 3, False)
(20, 3, False)
End game! Reward:  -1
You lost :(

(11, 7, False)
(16, 7, False)
(20, 7, False)
End game! Reward:  -1
You lost :(

(14, 6, False)
(18, 6, False)
End game! Reward:  -1.0
You lost :(



## Part 1: MC Prediction
In this section, you will write your own implementation of MC predction (for estimating the action-value function).

We will begin by investigating a policy where the player almost sticks if the sum of her cards exceeds 18. In particular, she select action STICK with 80% probability if the sum is greater than 18; and, if the sum is 18 or below, she selects action HIT with 80% probability. The function generate_episode_from_limit_stochastic samples an episode using this policy.

It returns as output:
* episode: This is a list of (state, action, reward) tuples (of tuples) and corresponds to $(S_0, A_0, R_1, \ldots, S_{T-1}, A_{T-1}, R_{T})$, where $T$ is the final time step. In particular, `episode[i]` returns $(S_i, A_i, R_{i+1})$, and `episode[i][0]`, `episode[i][1]`, and `episode[i][2]` return $S_i$, $A_i$, and $R_{i+1}$, repectively.

In [31]:
def generate_episode_from_limit_stochastic(bj_env):
  episode = []
  state = bj_env.reset()
  while True:
    probs = [0.8, 0.2] if state[0] > 18 else [0.2, 0.8]
    action = np.random.choice(np.arange(2), p=probs)
    next_state, reward, done, info = bj_env.step(action)
    episode.append((state, action, reward))
    state = next_state
    if done:
      break;
  return episode

In [32]:
for i in range(3):
  print(generate_episode_from_limit_stochastic(env))

[((13, 9, False), 1, 0), ((18, 9, False), 1, -1)]
[((14, 2, False), 1, 0), ((15, 2, False), 0, -1.0)]
[((5, 9, False), 1, 0), ((8, 9, False), 1, 0), ((14, 9, False), 1, -1)]


In [33]:
arr = np.array([1,2,3,4,5])
arr2 = np.array([1,2,3,4,5,6])
print(arr[3:], arr2[:-4], arr[2:], arr2[:-3])


[4 5] [1 2] [3 4 5] [1 2 3]


In [34]:
def mc_prediction_q(env, num_episodes, generate_episode, gamma=1.0):
  # initialize empty dictionaries of arrays
  returns_sum = defaultdict(lambda: np.zeros(env.action_space.n))
  N = defaultdict(lambda: np.zeros(env.action_space.n))
  Q = defaultdict(lambda: np.zeros(env.action_space.n))
  # loop over episodes
  for i_episode in range(1, num_episodes+1):
    # monitor progress
    if i_episode % 1000 == 0:
      print("\rEpisode {}/{}.".format(i_episode, num_episodes), end="")
      sys.stdout.flush()
    # generate an episode
    episode = generate_episode(env)
#     if i_episode % 1000 == 0:
#       print(episode[:2])
    # obtain the states, actions, and rewards
    states, actions, rewards = zip(*episode)
    # prepare for discounting
    discounts = np.array([gamma**i for i in range(len(rewards)+1)])
    # update the sum of the returns, number of visits, and action-value
    # function estimates for each state-action pair in the episode
    for i, state in enumerate(states):
      returns_sum[state][actions[i]] += sum(rewards[i:]*discounts[:-(1+i)])
      N[state][actions[i]] += 1.0
      Q[state][actions[i]] = returns_sum[state][actions[i]] / N[state][actions[i]]
  return Q

In [44]:
# obtain the action-value function
Q = mc_prediction_q(env, 50000, generate_episode_from_limit_stochastic)

first_item = next(iter(Q.items()))
print(first_item[0], first_item[1] )

# obtain the corresponding state-value functrion
V_to_plot = dict((k,(k[0]>18)*(np.dot([0.8, 0.2],v)) + (k[0]<=18)*(np.dot([0.2, 0.8],v))) \
         for k, v in Q.items())

# plot the state-value function
plt.rcParams['figure.dpi'] = 150
plot_blackjack_values(V_to_plot)

Episode 50000/50000.(16, 10, False) [-0.60110803 -0.68169209]


## Part 2: MC Control
In this section, you will write your own implementation of constant-$\alpha$ MC control.

Your algorithm has four arguments:
* `env`:  This is an instance of an OpenAI Gym environment.
* `num_episodes`: This is the number of episodes that are generated through agent-environment intersection.
* `alpha`: This is the step-size parameter for the update step.
* `gamma`: This is the discount rate. It must be a value between 0 and 1, inclusive (default value: 1).

The algorithm returns as output:
* `Q`: This is a dictionary (of one-dimentional arrays) where Q[`s`][`a`] is the estimated action value corresponding to state `s` and action `a`.
* policy: This is a dicitionary where `policy[s]`returns the action that the agent chooses after observing state `s`.

In [65]:
def generate_episode_from_Q(env, Q, epsilon, nA):
  """ generates an episode from following the epsilon-greedy policy"""
  episode = []
  state = env.reset()
  while True:
    action = np.random.choice(np.arange(nA), p=get_probs(Q[state], epsilon, nA)) \
                if state in Q else env.action_space.sample()
    next_state, reward, done, info = env.step(action)
    episode.append((state, action, reward))
    state = next_state
    if done:
      break
  return episode
  
def get_probs(Q_s, epsilon, nA):
  """ obtains the action probabilities corresponding to epsilon-greedy policy. """
  policy_s = np.ones(nA) * epsilon / nA
  best_a = np.argmax(Q_s)
  policy_s[best_a] = 1 - epsilon + (epsilon / nA)
  return policy_s

def update_Q(env, episode, Q, alpha, gamma):
  states, actions, rewards = zip(*episode)
  # prepare for discounting
  discounts = np.array([gamma**i for i in range(len(rewards)+1)])
  for i, state in enumerate(states):
    old_Q = Q[state][actions[i]]
    Q[state][actions[i]] = old_Q + alpha*(sum(rewards[i:]*discounts[:-(i+1)]) - old_Q)
  return Q



In [68]:
def mc_control(env, num_episodes, alpha, gamma=1.0, eps_start=1.0, eps_decay=.99999, eps_min=0.05):
  nA = env.action_space.n
  # initialize empty dictionary of array
  Q = defaultdict(lambda: np.zeros(nA))
  epsilon = eps_start
  # loop over eposides
  for i_episode in range(1, num_episodes+1):
    # monitor progress
    if i_episode % 1000 == 0:
      print('\rEpisode {}/{}.'.format(i_episode, num_episodes), end='')
      sys.stdout.flush()
    # set the value of epsilon
    epsilon = max(epsilon*eps_decay, eps_min)
    # generate an episode by following epsilon-greedy policy
    episode = generate_episode_from_Q(env, Q, epsilon, nA)
    # update the action-value function estimate using the episode
    Q = update_Q(env, episode, Q, alpha, gamma)
  # determine the policy corresponding to the final action-value function estimate
  policy = dict((k, np.argmax(v)) for k, v in Q.items())
  return policy, Q
  

In [69]:
# obtain the estimated optimal policy and action-value function
policy, Q = mc_control(env, 50000, 0.02)

Episode 50000/50000.

In [70]:
# obtain the corresponding state-value function
V = dict((k, np.max(v)) for k, v in Q.items())

# plot the state-value function
plot_blackjack_values(V)